<a href="https://colab.research.google.com/github/tchotaneu/Computer_vision/blob/main/Evaluation_des_Parametres_Optimales_de_Node2vec_Vue2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Nos Objectifs
Le but majeur de ce projet est d'identifier les meilleurs paramètres pour l'algorithme Node2Vec afin de produire des embeddings pour des graphes composés de deux Vues différentes. Chaque Vue est illustrée par un graphe non orienté. L'enjeu principal est de créer des embeddings qui reflètent avec précision les traits distinctifs et les aspects structurels de chaque perspective.




## Notre Approche:
Nous nous concentrerons sur l'optimisation des paramètres de sorte que les embeddings traduisent fidèlement la similarité parmi un ensemble prédéfini de 10 nœuds. Ces nœuds sont supposés constituer un module harmonieux au sein du graphe, que nous nommons "truehits".

# Partie 1 : Mise en place de l'environnement de travail

### **1.1-Installation de la bibliothèque Node2Vec**

#### *1.1.1 definition de node2vec*
Node2Vec est une méthode d'embedding pour les graphes, s'inspirant du célèbre Word2Vec conçu pour les textes. Son essence repose sur des marches aléatoires qui produisent des séquences de nœuds. Ces séquences sont ensuite transformées en embeddings, offrant des représentations continues et nuancées des nœuds. Les paramètres `p` et `q` jouent un rôle crucial, ajustant la nature des marches aléatoires pour explorer de manière équilibrée les aspects locaux et globaux du graphe.
#### *1.1.2 raison de notre de choix*
Contrairement à d'autres techniques d'embedding de graphes, Node2Vec se distingue par sa capacité à capturer simultanément des informations à différentes échelles. Cela le rend particulièrement adapté à une variété de tâches, allant de la classification des nœuds à la prédiction de liens, en passant par la visualisation des structures de graphes.

L'efficacité de Node2Vec est renforcée par sa flexibilité. Les utilisateurs peuvent ajuster ses paramètres pour s'adapter à des graphes de différentes natures et tailles. De plus, les embeddings générés peuvent être intégrés dans des architectures de machine learning plus larges, offrant ainsi une base solide pour des analyses complexes.
#### *1.1.3 comment l'utiliser*
Pour  exploiter le potentiel de cette méthode dans nos  projets d'analyse de graphes, l'installation de la bibliothèque Node2Vec est une étape neccessaire . Elle offre une interface intuitive et des outils pour faciliter le processus d'embedding, rendant l'analyse de graphes plus accessible et plus puissante.


In [1]:
!pip install node2vec    # Installer la bibliothèque node2vec

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 9.0 MB/s eta 0:00:00
  Attempting uninstall: networkx
    Found existing installation: networkx 3.1
    Uninstalling networkx-3.1:
      Successfully uninstalled networkx-3.1


### **1.2. Bibliothèques Python Essentielles pour Notre Projet de Génération d'Embeddings de Graphes**

Lorsqu'il s'agit de projets axés sur la génération et l'analyse d'embeddings de nœuds de graphe, s'appuyer sur les bonnes bibliothèques et modules Python est crucial. Ces outils offrent non seulement des fonctionnalités prêtes à l'emploi, mais aussi une base solide pour le développement, la mise en œuvre et l'évaluation de diverses méthodes et modèles. Voici quelques bibliothèques incontournables :

1. **networkx (nx)** : Une bibliothèque Python pour la création, la manipulation et l'étude des structures de graphes et des réseaux. Elle fournit des outils pour travailler avec des graphes simples et dirigés.

3. **os** : Fournit une interface pour interagir avec le système d'exploitation. Vous pouvez l'utiliser pour manipuler des chemins, créer des dossiers, lire des variables d'environnement, etc.

4. **ast** : Permet d'analyser le code source Python dans son arbre de syntaxe abstraite (AST). C'est utile pour la manipulation et l'analyse du code source.

5. **numpy (np)** : Une bibliothèque fondamentale pour les opérations mathématiques en Python. Elle fournit des structures de données pour les tableaux multidimensionnels et des fonctions pour effectuer des opérations sur ces tableaux.

6. **itertools.product** : Génère le produit cartésien de listes ou d'itérables. C'est utile pour créer des combinaisons de paramètres ou d'autres listes.

7. **node2vec** : Une bibliothèque pour générer des embeddings de nœuds dans des graphes en utilisant l'algorithme Node2Vec.

8. **sklearn.model_selection.ParameterGrid** : Utile pour créer une grille de paramètres pour la recherche sur grille, souvent utilisée en apprentissage automatique pour trouver les meilleurs paramètres pour un modèle.

9. **sklearn.metrics.pairwise.cosine_similarity** : Calcule la similarité cosinus entre des vecteurs, souvent utilisée pour comparer des embeddings ou d'autres vecteurs en apprentissage automatique.

10. **google.colab** : Si vous travaillez sur Google Colab, ce module fournit des fonctions pour interagir avec l'environnement Colab, comme le chargement de fichiers, l'affichage de graphiques, etc. Cependant, la ligne est incomplète, donc je ne peux pas déterminer exactement quelle fonctionnalité de `google.colab` vous souhaitez utiliser.


In [5]:
import networkx as nx # Importer la bibliothèque NetworkX pour la création, la manipulation et l'étude de la structure, de la dynamique et des fonctions des réseaux complexes.
import os # Importer le module os pour interagir avec le système d'exploitation, notamment pour accéder aux variables d'environnement et gérer les chemins de fichiers.
import ast # Importer le module ast pour traiter les arbres de syntaxe abstraite Python.
import pandas as pd
import numpy as np  # Importer la bibliothèque NumPy pour la manipulation de tableaux et matrices, et pour effectuer des opérations mathématiques avancées.
from itertools import product # Importer le module product de itertools pour générer des produits cartésiens.
from node2vec import Node2Vec # Importer la bibliothèque Node2Vec pour générer des embeddings de nœuds dans un graphe.
from sklearn.model_selection import ParameterGrid # Importer ParameterGrid de sklearn.model_selection pour créer une grille de paramètres pour la recherche sur grille.
from sklearn.metrics.pairwise import cosine_similarity # Importer cosine_similarity de sklearn.metrics.pairwise pour calculer la similarité cosinus entre les embeddings de nœuds.
from google.colab import drive# Importer le module drive de google.colab pour monter Google Drive.


### **1.3 .Monter Notre Drive**

Dans tout projet d'analyse de données ou d'apprentissage automatique, la sauvegarde régulière des résultats est cruciale. Cela est particulièrement vrai lorsque les temps de calcul sont longs, car toute interruption ou erreur inattendue peut entraîner la perte d'heures, voire de jours, de travail. En travaillant sur Google Colab, une solution efficace est de monter notre Google Drive directement dans l'environnement Colab. Cela nous permet non seulement de sauvegarder nos résultats en temps réel dans un espace de stockage persistant et de profiter de la puissance de calcul offert gratuitement par google, mais aussi d'accéder facilement à ces résultats à partir de n'importe quel appareil connecté à notre compte Google. Dans cette section, nous allons mettre en place cette intégration et garantir que nos précieuses données et résultats sont sauvegardés en toute sécurité.

In [3]:
# Montez notre Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


# Partie 2: Définir les Fonctions

L'efficacité et la modularité d'un projet reposent souvent sur une bonne organisation du code. En décomposant notre projet en fonctions spécifiques, nous pouvons non seulement rendre notre code plus lisible, mais aussi faciliter la réutilisation et la modification de certaines parties du code à l'avenir. Dans cette section, nous allons définir trois fonctions essentielles qui serviront de pierres angulaires à notre analyse :

1. definir une fonction pour evaluer notre modele sur le groupe de noeud predefinir

2. definir une fonctiion pour contruire le modele avec les  parameretre choisir dans dans la grille de parametres

3. une fonction pour recuperer noutre module actif dans le drive



### 2.1 **la fonction pour l'Évaluation du Modèle** :

Cette fonction évaluera la qualité de nos embeddings sur un ensemble prédéfini de nœuds en utilisant la similarité cosinus comme métrique principale. Deux critères clés seront utilisés pour cette évaluation :
1. La similarité cosinus moyenne de l'ensemble du groupe, reflétant la cohérence globale des embeddings au sein du groupe.
2. La similarité cosinus minimale observée au sein du groupe, qui nous indiquera la paire de nœuds la moins similaire et nous aidera à identifier les éventuelles anomalies ou outliers.

Ces deux critères nous permettront d'avoir une vue d'ensemble de la performance de notre modèle et de comprendre sa capacité à capturer fidèlement les relations intra-groupe.




In [61]:
def evaluate_model(model, nodeGroup):
    """
    Évalue un modèle d'embedding en calculant la similarité cosinus moyenne et minimale
    entre les embeddings de tous les nœuds dans un groupe de nœuds donné.

    :param model: Le modèle d'embedding à évaluer.
    :param nodeGroup: Un groupe de nœuds pour lesquels calculer la similarité.
    :return: Un tuple contenant la similarité cosinus moyenne et minimale entre les embeddings de nœuds.
    """

    # Obtenir les embeddings pour chaque nœud dans le groupe de nœuds
    embeddings = np.array([model.wv[str(node)] for node in nodeGroup])

    # Calculer la matrice de similarité cosinus entre les embeddings
    similarity_matrix = cosine_similarity(embeddings)

    # Extraire la moitié supérieure de la matrice sans la diagonale  car la matrice de similarité est symétrique et la diagonale est toujours 1
    upper_triangle = similarity_matrix[np.triu_indices(similarity_matrix.shape[0], k=1)]

    # Calculer la similarité moyenne et minimale de la moitié supérieure
    avg_similarity = np.mean(upper_triangle)
    min_similarity = np.min(upper_triangle)

    return avg_similarity, min_similarity



###  **2.2 la fonction pour la Construction de notre Modèle** :

cette fonction offrira la flexibilité de construire notre modèle d'embedding node2vec  selon les paramètres souhaités dans une plage defini. Cela serait  un atout majeur pour  nous d'expérimenter diverses configurations avce notre de grille de parametres .




In [64]:

def evaluate_parameter(graphe, nodeGroup, paramGrille, fichier_csv):
    """

    """

    # Initialisation des seuils de similarité
    avg_similarite_threshold = 0.65
    min_similarite_threshold = 0.65

    # Itérer sur toutes les combinaisons de paramètres dans la grille
    for params in paramGrille:
        params_Node2vec = {key: params[key] for key in ['dimensions', 'walk_length', 'num_walks', 'p', 'q']}
        node2vec = Node2Vec(graphe, **params_Node2vec)
        model = node2vec.fit(window=params['window'], min_count=1, sg=1, alpha=params['learning_rate'])

        avg_similarite, min_similarite = evaluate_model(model, nodeGroup)  # Assurez-vous que cette fonction est correctement définie ailleurs

        # Créer un DataFrame pour les résultats actuels
        df_current = pd.DataFrame({
            'params': [str(params)],
            'avg_similarite': [avg_similarite],
            'min_similarite': [min_similarite]
        })

        # Écrire les résultats actuels à la fin du fichier CSV
        with open(fichier_csv, 'a+') as f:
            df_current.to_csv(f, header=f.tell() == 0, index=False)

        # Afficher les résultats qui satisfont les seuils
        if (avg_similarite >= avg_similarite_threshold) and (min_similarite >= min_similarite_threshold):
            print(f"Paramètres : {params} | Moyenne : {avg_similarite} | Minimum : {min_similarite}")


### 2.3 Fonction de Récupération des Nœuds "True Hits"

La fonction que nous allons développer dans cette section aura pour objectif de récupérer efficacement les nœuds appartenant au groupe "True Hits". En ayant une méthode dédiée à cette tâche, nous nous assurons d'une extraction cohérente et fiable de ces nœuds à chaque fois que nous en avons besoin, évitant ainsi les erreurs manuelles et garantissant la reproductibilité de nos analyses.



In [65]:
def load_true_hit(fichier_csv,ligne,champ='Truehit', cle='1'):
    """
    Récupère une valeur d'un dictionnaire situé dans une colonne spécifiée de la première ligne d'un fichier CSV.

    :param fichier_csv: Le chemin du fichier CSV.
    :param champ: Le nom de la colonne contenant le dictionnaire.
    :param cle: La clé à rechercher dans le dictionnaire.
    :return: La valeur associée à la clé dans le dictionnaire, ou None si la clé n'est pas présente.
    """

    # Charger le fichier CSV dans un DataFrame
    df = pd.read_csv(fichier_csv)
    # Récupérer le dictionnaire de la première ligne de la colonne spécifiée
    dictionnaire_str = df[champ].iloc[ligne]
    dictionnaire = ast.literal_eval(dictionnaire_str)
    # Récupérer la valeur associée à la clé, si elle est présente
    valeur = dictionnaire.get(cle, None)

    if valeur is not None:
      return list(valeur)
    return valeur




### 2.4 Fonction de Chargement du Graphe

La manipulation et l'analyse de graphes nécessitent une première étape cruciale : le chargement du graphe depuis une source de données. Dans notre cas, le graphe est stocké dans un fichier texte, structuré de manière à ce que chaque ligne décrive un nœud et ses connexions.

Dans cette section, nous allons développer une fonction dédiée au chargement de ce graphe. Cette fonction lira le fichier texte ligne par ligne, interprétera chaque ligne pour identifier le nœud principal et ses voisins, puis construira progressivement le graphe en ajoutant les nœuds et leurs relations respectives.

En disposant d'une telle fonction, nous nous assurons d'une initialisation correcte et uniforme du graphe à chaque fois que nous démarrons une nouvelle analyse ou expérimentation. Cette standardisation est essentielle pour garantir la reproductibilité de nos résultats et pour éviter les erreurs potentielles liées à une mauvaise interprétation du fichier source.

In [66]:
def load_graph(filename: str) -> nx.Graph:
        G_reconstructed = nx.Graph()
        with open(filename, 'r') as f:
            mode = None  # Utilisé pour savoir si nous lisons un nœud ou une arête
            for line in f.readlines():
                line = line.strip()
                if line.startswith("#"):
                    mode = line[2:].lower()  # Définir le mode sur 'nodes' ou 'edges' en fonction du commentaire
                    continue

                parts = line.split()
                if mode == 'nodes':
                    _, node, weight = parts
                    G_reconstructed.add_node(node, weight=float(weight))
                elif mode == 'edges':
                    _, u, v, weight = parts
                    G_reconstructed.add_edge(u, v, weight=int(weight))
        return G_reconstructed

### 2.4 Fonction de Construction de la Seconde Vue du Graphe

Comme nous l'avons mention au debu de notre projet nous travaillaons sur un graphe a plusieurs vue .l'experimentation  de travail avec  plusieurs "vues" ou représentations d'un même graphe, permet de mettres en evidence des aspects ou des caractéristiques différentes. Dans notre contexte, après avoir travaillé avec une première vue du graphe, nous souhaitons construire une seconde vue à partir de celle-ci.

Dans cette section, nous élaborerons une fonction spécifiquement dédiée à cette transformation. Cette fonction prendra en entrée la première vue du graphe et appliquera un ensemble de règles ou d'algorithmes pour générer la seconde vue. Cette seconde vue pourrait, par exemple, mettre en évidence des relations secondaires sur la pvalue de noeuds ou sur les poids des noeuds , en d'autre terme nous allons filtre le graphe en fonctions des pvalue des noeud

En centralisant cette étape de transformation dans une fonction dédiée, nous nous assurons d'une transition cohérente et contrôlée entre les deux vues. Cela garantit que la seconde vue est toujours construite de manière uniforme, indépendamment des modifications ou des évolutions de la première vue, assurant ainsi la stabilité et la reproductibilité de nos analyses ultérieures.

In [67]:
def construct_graph1(self, G: nx.Graph, p_value: float = 0.05) -> nx.Graph:
        """
        Construit un nouveau graphe basé sur le graphe d'origine G, en extrayant les composantes connexes
        des nœuds avec un poids inférieur à p_value.

        :param G: Le graphe d'origine.
        :param p_value: La valeur de p utilisée pour filtrer les nœuds.
        :return: Le nouveau graphe construit.
        """

            # Créer un nouveau graphe
        G_prime = nx.Graph()

            # Ajouter tous les nœuds de G à G_prime
        G_prime.add_nodes_from(G.nodes(data=True))
            # Parcourir toutes les arêtes dans G et les ajouter à G_prime si les deux nœuds ont une p_value < 0.05
        for u, v,data in G.edges(data=True):
            u_data = G.nodes[u]["weight"]
            v_data = G.nodes[v]["weight"]

            if u_data <= p_value and v_data <= p_value:
                G_prime.add_edge(u, v, **data)

        return G_prime


def construct_graph2(self, G: nx.Graph, p_value: float = 0.05 ,singleton:bool=True) -> nx.Graph:
        """
        Construit un graphe complet entre les nœuds avec un poids inférieur à p_value.

        :param G: Le graphe d'origine.
        :param p_value: La valeur de p utilisée pour filtrer les nœuds.
        :return: Le nouveau graphe construit.
        """
        G_prime = nx.Graph()
        G_prime.add_nodes_from(G.nodes(data=True))
        nodes_singletons = [(node, data) for node, data in G.nodes(data=True) if data['weight'] > p_value]
        nodes_pvalue = [node for node, data in G.nodes(data=True) if data['weight'] <= p_value]
        G_prime.add_edges_from((u, v) for i, u in enumerate(nodes_pvalue) for v in nodes_pvalue[i + 1:])
        if singleton:
            G_prime.add_nodes_from(nodes_singletons)
        return G_prime

charge le fichier deje enregistres

In [76]:
def load_or_create_csv(fichier_csv):
    """
    Récupère les combinaisons de paramètres déjà évaluées à partir d'un fichier CSV.

    :param fichier_csv: Le chemin du fichier CSV contenant les résultats précédents.
    :return: Une liste de dictionnaires représentant les combinaisons de paramètres déjà évaluées.
    """

    # Vérifier si le fichier CSV existe
    if not os.path.exists(fichier_csv):
        # Si le fichier n'existe pas, créer un nouveau dataframe avec les colonnes spécifiées et le sauvegarder en tant que CSV.
        print(f"Le fichier {fichier_csv} n'existe pas. Création du fichier...")
        df_modeles = pd.DataFrame(columns=['params', 'avg_similarite', 'min_similarite'])
        df_modeles.to_csv(fichier_csv, index=False)
        print(f"Fichier {fichier_csv} créé avec succès !")
        return []

    # Charger le fichier CSV
    df = pd.read_csv(fichier_csv)

    # Si le fichier est vide ou ne contient pas la colonne 'params', renvoyer une liste vide
    if df.empty or 'params' not in df.columns:
        return []

    # Extraire les combinaisons de paramètres et les convertir en liste de dictionnaires
    params_deja_evalues = [eval(params_str) for params_str in df['params'].unique()]

    return params_deja_evalues


# Partie3 : execution



#### 3.1 definition de la grille de parametres .

1. dimensions 'dimensions': [32,48], est le  Nombre de dimensions de l'espace d'embedding.
2. 'walk_length': [30,65,100],  # Nombre de nœuds dans chaque marche aléatoire.
3. 'num_walks': [10,20,30],  # Nombre de marches aléatoires à partir de chaque nœud.
4. 'p': [0.25, 0.5,1,1.5],  # Paramètre qui contrôle la probabilité de sauter à un voisin proche.
5.   'q': [0.25,0.5,1,1.5],  # Paramètre qui contrôle la probabilité de sauter à un voisin lointain.
6.   'window': [5,7, 10],  # Taille de la fenêtre contextuelle pour le modèle Skip-gram.
7. 'learning_rate': [0.001, 0.005]  # Taux d'apprentissage pour l'optimisation.



In [70]:

paramGrille = {
    'dimensions': [32,48, 64],  # Nombre de dimensions de l'espace d'embedding.
    'walk_length': [20,30,50],  # Nombre de nœuds dans chaque marche aléatoire.
    'num_walks': [10,20,30],  # Nombre de marches aléatoires à partir de chaque nœud.
    'p': [0.25, 0.5,1,1.5],  # Paramètre qui contrôle la probabilité de sauter à un voisin proche.
    'q': [0.25,0.5,1,1.5],  # Paramètre qui contrôle la probabilité de sauter à un voisin lointain.
    'window': [5,7, 10],  # Taille de la fenêtre contextuelle pour le modèle Skip-gram.
    'learning_rate': [0.001, 0.005]  # Taux d'apprentissage pour l'optimisation.
}

### 3.2 Chargement du Graphe et Construction de la Seconde Vue

L'analyse de données basée sur des graphes commence par une étape fondamentale  le chargement du graphe depuis sa source.

Dans cette section, nous commencerons par charger notre graphe depuis le fichier source où il est stocké. Une fois ce graphe initial en place, nous entreprendrons la construction de sa seconde vue.

Cette démarche séquentielle, du chargement initial à la transformation, nous permet de travailler avec des données structurées de manière flexible.

### 3.3 Chemin de Sauvegarde des Modèles

Travailler dans un environnement à sessions temporaires, comme Google Colab, nécessite une sauvegarde proactive. Les interruptions peuvent survenir, risquant la perte de données précieuses. Dans cette section, nous établirons un chemin de sauvegarde pour nos modèles, idéalement vers notre Google Drive. Cette démarche garantit que, malgré les interruptions, notre progression est conservée. De plus, un emplacement dédié facilite la gestion des versions, permettant des comparaisons et des analyses basées sur des modèles antérieurs.



In [86]:
# Spécifier le chemin du dossier dans Google Drive où sauvegarder/charger le fichier.
# Spécifier le nom du fichier à charger.
my_model_file = '/content/drive/MyDrive/stage_I3S/les_modeles.csv'
param_deja = load_or_create_csv( my_model_file )

Le fichier /content/drive/MyDrive/stage_I3S/les_modeles.csv n'existe pas. Création du fichier...
Fichier /content/drive/MyDrive/stage_I3S/les_modeles.csv créé avec succès !


In [81]:

print(param_deja)

[]


### 3.4 Réduction de la Grille de Paramètres

 la recherche sur grille est une méthode courante pour explorer différentes combinaisons de paramètres. comme nous travaillons dans in  environnement à sessions temporaires, il est possible que certains paramètres aient déjà été évalués lors de sessions précédentes. Pour éviter des redondances et gagner du temps, il est judicieux de filtrer la grille de paramètres en éliminant les combinaisons déjà évaluées. Cette approche nous permettra de concentrer nos ressources sur l'évaluation de nouvelles combinaisons, optimisant ainsi notre processus d'exploration.

In [82]:
new_paramGrille = list(filter(lambda p: p not in param_deja, ParameterGrid(paramGrille)))
# Imprimer la nouvelle grille de paramètres après avoir exclu les paramètres déjà évalués.
print(new_paramGrille)
# Imprimer la longueur de la nouvelle grille de paramètres, c'est-à-dire le nombre de combinaisons de paramètres restantes à évaluer.
print(len(new_paramGrille))


[{'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 20, 'window': 5}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 20, 'window': 7}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 20, 'window': 10}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 30, 'window': 5}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 30, 'window': 7}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 30, 'window': 10}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 50, 'window': 5}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0.25, 'walk_length': 50, 'window': 7}, {'dimensions': 32, 'learning_rate': 0.001, 'num_walks': 10, 'p': 0.25, 'q': 0

# lancons le execution

### recuperation des graphe .

In [83]:
# Créer ou charger un graphe en utilisant NetworkX.
# 'nx.read_edgelist' lit les listes d'arêtes d'un fichier et crée un graphe non dirigé.
# Le chemin du fichier contenant la liste d'arêtes est spécifié.
chemin_graphe = "/content/drive/MyDrive/stage_I3S/mane_avecgrap1/mane_zip1/dataset/Vue2.txt"
graphe=load_graph(chemin_graphe)

for node, data in graphe.nodes(data=True):
    if 'weight' in data:
        del data['weight']

# Vérifier que les poids ont été supprimés
print(graphe.edges(data=True))


[('30', '680', {'weight': 1}), ('30', '120', {'weight': 1}), ('30', '714', {'weight': 1}), ('30', '925', {'weight': 1}), ('30', '731', {'weight': 1}), ('31', '37', {'weight': 1}), ('31', '409', {'weight': 1}), ('37', '533', {'weight': 1}), ('37', '129', {'weight': 1}), ('37', '409', {'weight': 1}), ('103', '108', {'weight': 1}), ('103', '838', {'weight': 1}), ('108', '362', {'weight': 1}), ('108', '120', {'weight': 1}), ('115', '216', {'weight': 1}), ('120', '239', {'weight': 1}), ('129', '330', {'weight': 1}), ('129', '873', {'weight': 1}), ('129', '604', {'weight': 1}), ('132', '604', {'weight': 1}), ('132', '273', {'weight': 1}), ('160', '239', {'weight': 1}), ('177', '264', {'weight': 1}), ('177', '838', {'weight': 1}), ('177', '680', {'weight': 1}), ('190', '731', {'weight': 1}), ('216', '854', {'weight': 1}), ('240', '264', {'weight': 1}), ('264', '535', {'weight': 1}), ('330', '870', {'weight': 1}), ('364', '481', {'weight': 1}), ('680', '873', {'weight': 1}), ('809', '873', {'w

#### recuperation du truets hits correspondants

In [84]:
chemintruehit="/content/drive/MyDrive/stage_I3S/mane_avecgrap1/resultats/mon_fichier.csv"
truehits=load_true_hit(fichier_csv=chemintruehit,ligne=0, champ='Truehits', cle=1)


In [85]:
print(truehits)

[129, 37, 680, 809, 330, 873, 143, 120, 30, 895]


### execution du modele

In [ ]:
lesModels = evaluate_parameter(graphe,truehits,new_paramGrille ,my_model_file)

Computing transition probabilities:   0%|          | 0/1000 [00:00<?, ?it/s]

Generating walks (CPU: 1): 100%|██████████| 10/10 [00:00<00:00, 185.79it/s]


Computing transition probabilities:   0%|          | 0/1000 [00:00<?, ?it/s]

Generating walks (CPU: 1): 100%|██████████| 10/10 [00:00<00:00, 177.80it/s]


Computing transition probabilities:   0%|          | 0/1000 [00:00<?, ?it/s]

...

Generating walks (CPU: 1): 100%|██████████| 30/30 [00:00<00:00, 44.38it/s]


Computing transition probabilities:   0%|          | 0/1000 [00:00<?, ?it/s]

Generating walks (CPU: 1): 100%|██████████| 30/30 [00:00<00:00, 109.40it/s]


Computing transition probabilities:   0%|          | 0/1000 [00:00<?, ?it/s]

Generating walks (CPU: 1): 100%|██████████| 30/30 [00:00<00:00, 120.69it/s]
